<a href="https://www.kaggle.com/code/klyushnik/weight-regression-keras?scriptVersionId=196336106" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/playground-series-s4e9/sample_submission.csv
/kaggle/input/playground-series-s4e9/train.csv
/kaggle/input/playground-series-s4e9/test.csv


# Description

![072919-RL-Average-car-price-SEO-refresh_Graph_WP_1540x1000.jpg?w=1024](https://roadloans.com/wp-content/uploads/2018/03/072919-RL-Average-car-price-SEO-refresh_Graph_WP_1540x1000.jpg?w=1024)

**Welcome to the 2024 Kaggle Playground Series!** We plan to continue in the spirit of previous playgrounds, providing interesting an approachable datasets for our community to practice their machine learning skills, and anticipate a competition each month.

**Your Goal: The goal of this competition is to predict the price of used cars based on various attributes.**

**Evaluation
Root Mean Squared Error (RMSE)**
**Submissions are scored on the root mean squared error. RMSE is defined as:**

![RMSE1.jpg](https://media.geeksforgeeks.org/wp-content/uploads/20200622171741/RMSE1.jpg)

**About Dataset**
**Used Car Price Prediction Dataset is a comprehensive collection of automotive information extracted from the popular automotive marketplace website, https://www.cars.com. This dataset comprises 4,009 data points, each representing a unique vehicle listing, and includes nine distinct features providing valuable insights into the world of automobiles.**

* Brand & Model: Identify the brand or company name along with the specific model of each vehicle.
* Model Year: Discover the manufacturing year of the vehicles, crucial for assessing depreciation and technology advancements.
* Mileage: Obtain the mileage of each vehicle, a key indicator of wear and tear and potential maintenance requirements.
* Fuel Type: Learn about the type of fuel the vehicles run on, whether it's gasoline, diesel, electric, or hybrid.
* Engine Type: Understand the engine specifications, shedding light on performance and efficiency.
* Transmission: Determine the transmission type, whether automatic, manual, or another variant.
* Exterior & Interior Colors: Explore the aesthetic aspects of the vehicles, including exterior and interior color options.
* Accident History: Discover whether a vehicle has a prior history of accidents or damage, crucial for informed decision-making.
* Clean Title: Evaluate the availability of a clean title, which can impact the vehicle's resale value and legal status.
* Price: Access the listed prices for each vehicle, aiding in price comparison and budgeting.
**This dataset is a valuable resource for automotive enthusiasts, buyers, and researchers interested in analyzing trends, making informed purchasing decisions or conducting studies related to the automotive industry and consumer preferences. Whether you are a data analyst, car buyer, or researcher, this dataset offers a wealth of information to explore and analyze.**

**API comand** - kaggle datasets download -d taeefnajib/used-car-price-prediction-dataset

# Welcome

**Welcome to my github - https://github.com/Alexsandrrus/projekts-Kaggle**

# Imports

In [2]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib as mpl
import warnings
warnings.filterwarnings('ignore')
from IPython.display import Image
%matplotlib inline


import tensorflow as tf
import keras
from keras import layers
import re
from keras.layers import BatchNormalization, Flatten, Dense, Dropout, Activation
import keras
import keras_tuner
from tensorflow.keras.models import Sequential
from keras import backend as K

from scipy.optimize import minimize

from sklearn.linear_model import SGDOneClassSVM
from sklearn.neighbors import LocalOutlierFactor
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.decomposition import PCA
from sklearn.metrics import mean_squared_error
from sklearn.pipeline import Pipeline
from sklearn.impute import KNNImputer, SimpleImputer
from sklearn.ensemble import (HistGradientBoostingRegressor,ExtraTreesRegressor,
                              GradientBoostingRegressor, IsolationForest, BaggingRegressor)
from sklearn.model_selection import (StratifiedKFold, KFold, StratifiedGroupKFold, RepeatedStratifiedKFold,
                                     RepeatedKFold, cross_validate,train_test_split)
from sklearn.preprocessing import (LabelEncoder, QuantileTransformer, StandardScaler,
                                   PowerTransformer,MaxAbsScaler,MinMaxScaler,
                                   RobustScaler,PolynomialFeatures, StandardScaler, label_binarize, PolynomialFeatures,
                                  OrdinalEncoder)
from sklearn import preprocessing
from sklearn.feature_selection import (VarianceThreshold, SequentialFeatureSelector, f_regression)
from sklearn.metrics import mean_absolute_error
from sklearn.linear_model import LinearRegression

import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
from functools import partial
from itertools import combinations
from ydata_profiling import ProfileReport

import optuna
from optuna.samplers import CmaEsSampler
from catboost import CatBoostRegressor
import xgboost as xgb
from lightgbm import LGBMRegressor
import time
from functools import partial

In [3]:
random_state = 42
n_splits = 5

def PolynomialFeatures_labeled(input_df,power):
   
    poly = PolynomialFeatures(power)
    output_nparray = poly.fit_transform(input_df)
    powers_nparray = poly.powers_

    input_feature_names = list(input_df.columns)
    target_feature_names = ["Constant Term"]
    for feature_distillation in powers_nparray[1:]:
        intermediary_label = ""
        final_label = ""
        for i in range(len(input_feature_names)):
            if feature_distillation[i] == 0:
                continue
            else:
                variable = input_feature_names[i]
                power = feature_distillation[i]
                intermediary_label = "%s+%d" % (variable,power)
                if final_label == "":         #If the final label isn't yet specified
                    final_label = intermediary_label
                else:
                    final_label = final_label + "x" + intermediary_label
        target_feature_names.append(final_label)
    output_df = pd.DataFrame(output_nparray, columns = target_feature_names)
    return output_df

def variance_threshold(df,th):
    var_thres=VarianceThreshold(threshold=th)
    var_thres.fit(df)
    new_cols = var_thres.get_support()
    return df.iloc[:,new_cols]

def extract_age_features(df):
    current_year = 2024
    df['Vehicle_Age'] = current_year - df['model_year']
    df['Mileage_per_Year'] = df['milage'] / df['Vehicle_Age']
    df['milage_with_age'] =  df.groupby('Vehicle_Age')['milage'].transform('mean')
    df['Mileage_per_Year_with_age'] =  df.groupby('Vehicle_Age')['Mileage_per_Year'].transform('mean')    
    return df

# Dataset

In [4]:
train = pd.read_csv('/kaggle/input/playground-series-s4e9/train.csv')
test = pd.read_csv('/kaggle/input/playground-series-s4e9/test.csv')

print(f'Shape train is {train.shape} and shape test is{test.shape}')

Shape train is (188533, 13) and shape test is(125690, 12)


In [5]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 188533 entries, 0 to 188532
Data columns (total 13 columns):
 #   Column        Non-Null Count   Dtype 
---  ------        --------------   ----- 
 0   id            188533 non-null  int64 
 1   brand         188533 non-null  object
 2   model         188533 non-null  object
 3   model_year    188533 non-null  int64 
 4   milage        188533 non-null  int64 
 5   fuel_type     183450 non-null  object
 6   engine        188533 non-null  object
 7   transmission  188533 non-null  object
 8   ext_col       188533 non-null  object
 9   int_col       188533 non-null  object
 10  accident      186081 non-null  object
 11  clean_title   167114 non-null  object
 12  price         188533 non-null  int64 
dtypes: int64(4), object(9)
memory usage: 18.7+ MB


In [6]:
train.isna().sum()

id                  0
brand               0
model               0
model_year          0
milage              0
fuel_type        5083
engine              0
transmission        0
ext_col             0
int_col             0
accident         2452
clean_title     21419
price               0
dtype: int64

In [7]:
train.duplicated().sum()

0

In [8]:
test.isna().sum()

id                  0
brand               0
model               0
model_year          0
milage              0
fuel_type        3383
engine              0
transmission        0
ext_col             0
int_col             0
accident         1632
clean_title     14239
dtype: int64

# ProfileReport

In [9]:
profile = ProfileReport(train, title="Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# More information

In [10]:
train = extract_age_features(train)
test = extract_age_features(test)

In [11]:
new_df = train['engine'].str.split(' ',expand=True)
new_df.columns=['horsepower','engine_dis_L','Cylinder','name_Cylinder','name2','name3','1','2','3']
new_df

horsepower engine_dis_L Cylinder name_Cylinder   name2     name3     1  \
0         172.0HP         1.6L        4      Cylinder  Engine  Gasoline  Fuel   
1         252.0HP         3.9L        8      Cylinder  Engine  Gasoline  Fuel   
2         320.0HP         5.3L        8      Cylinder  Engine      Flex  Fuel   
3         420.0HP         5.0L        8      Cylinder  Engine  Gasoline  Fuel   
4         208.0HP         2.0L        4      Cylinder  Engine  Gasoline  Fuel   
...           ...          ...      ...           ...     ...       ...   ...   
188528    420.0HP         6.2L        8      Cylinder  Engine  Gasoline  Fuel   
188529    385.0HP         3.0L       V6      Cylinder  Engine  Gasoline  Fuel   
188530    469.0HP         4.0L        8      Cylinder  Engine  Gasoline  Fuel   
188531       3.0L         None     None          None    None      None  None   
188532    252.0HP         2.0L        4      Cylinder  Engine  Gasoline  Fuel   

                 2     3  
0             None  None  
1             None  None  
2       Capability  None  
3             None  None  
4             None  None  
...            ...   ...  
188528        None  None  
188529        None  None  
188530        None  None  
188531        None  None  
188532        None  None  

[188533 rows x 9 columns]

In [12]:
train['horsepower'] = new_df['horsepower'].str.replace('HP|L|V|Ah|I', '', regex=True)
train['horsepower'] = train['horsepower'].str.replace('Electric|Dual|-|Intercooled|Standard|Battery|ntercooled', '0', regex=True)
train['horsepower'] = train['horsepower'].str.replace('–', '0', regex=True)
train['horsepower']= train['horsepower'].astype(float)

train['engine_dis_L'] = new_df['engine_dis_L'].str.replace('HP|L|V|Ah|I|W|H|C', '', regex=True)
train['engine_dis_L'] = train['engine_dis_L'].str.replace('Motor|Electric|-|None|Turbo|Range|Cylinder|AH|/|iter|A|ylinder', '0', regex=True)
train['engine_dis_L'] = train['engine_dis_L'].str.replace('–', '0', regex=True)
train['engine_dis_L']= train['engine_dis_L'].astype(float)

In [13]:
new_df_test = test['engine'].str.split(' ',expand=True)
new_df_test.columns=['horsepower','engine_dis_L','Cylinder','name_Cylinder','name2','name3','1','2','3']
display(new_df_test)

test['horsepower'] = new_df_test['horsepower'].str.replace('HP|L|V|Ah|I', '', regex=True)
test['horsepower'] = test['horsepower'].str.replace('Electric|Dual|-|Intercooled|Standard|Battery|ntercooled', '0', regex=True)
test['horsepower'] = test['horsepower'].str.replace('–', '0', regex=True)
test['horsepower']= test['horsepower'].astype(float)

test['engine_dis_L'] = new_df_test['engine_dis_L'].str.replace('HP|L|V|Ah|I|W|H|C', '', regex=True)
test['engine_dis_L'] = test['engine_dis_L'].str.replace('Motor|Electric|-|None|Turbo|Range|Cylinder|AH|/|iter|A|ylinder', '0', regex=True)
test['engine_dis_L'] = test['engine_dis_L'].str.replace('–', '0', regex=True)
test['engine_dis_L']= test['engine_dis_L'].astype(float)

horsepower engine_dis_L  Cylinder name_Cylinder     name2     name3  \
0         240.0HP         2.0L         4      Cylinder    Engine  Gasoline   
1         395.0HP         3.0L  Straight             6  Cylinder    Engine   
2            3.5L           V6       24V           PDI      DOHC      Twin   
3             2.0        Liter      TFSI          None      None      None   
4         252.0HP         2.0L         4      Cylinder    Engine  Gasoline   
...           ...          ...       ...           ...       ...       ...   
125685    362.0HP         3.0L        V6      Cylinder    Engine  Gasoline   
125686        3.0        Liter     Turbo          None      None      None   
125687    333.0HP         3.0L        V6      Cylinder    Engine  Gasoline   
125688    333.0HP         3.0L        V6      Cylinder    Engine  Gasoline   
125689    355.0HP         5.3L         8      Cylinder    Engine  Gasoline   

                    1         2       3  
0                Fuel      None    None  
1       Gasoline/Mild  Electric  Hybrid  
2               Turbo      None    None  
3                None      None    None  
4                Fuel      None    None  
...               ...       ...     ...  
125685           Fuel      None    None  
125686           None      None    None  
125687           Fuel      None    None  
125688           Fuel      None    None  
125689           Fuel      None    None  

[125690 rows x 9 columns]

# Preparing data and train, test split

In [14]:
num_rows = len(train.index)
low_information_cols = [] #

for col in train.columns:
    cnts = train[col].value_counts(dropna=False)
    top_pct = (cnts/num_rows).iloc[0]
    
    if top_pct > 0.95:
        low_information_cols.append(col)
        print('{0}: {1:.5f}%'.format(col, top_pct*100))
        print(cnts)
        print()

In [15]:
numetric_list = list(train.select_dtypes(include=[np.number]).columns)
numetric_list.pop(3)
numetric_list.pop(0)

numetric_list

['model_year',
 'milage',
 'Vehicle_Age',
 'Mileage_per_Year',
 'milage_with_age',
 'Mileage_per_Year_with_age',
 'horsepower',
 'engine_dis_L']

In [16]:
X = train.drop(columns = ['id', 'price'], axis =1)
y = train['price']
X_total = test.drop(columns = ['id'], axis =1)

enc = OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=-1)
org_cat_col = X.select_dtypes(include='object').columns
    
X[org_cat_col] = enc.fit_transform(X[org_cat_col].astype(str))
X_total[org_cat_col] = enc.transform(X_total[org_cat_col].astype(str))

X_nan_col = X.columns[X.isna().any()].tolist()
X_total_nan = X_total.columns[X_total.isna().any()].tolist()
columns_with_nan = list(set(X_nan_col) | set(X_total_nan))

KNN_imputer = KNNImputer(n_neighbors=5)
X[columns_with_nan] = KNN_imputer.fit_transform(X[columns_with_nan])
X_total[columns_with_nan] = KNN_imputer.transform(X_total[columns_with_nan])

X = X.replace((np.inf, -np.inf, np.nan), 0).reset_index(drop=True)
X_total = X_total.replace((np.inf, -np.inf, np.nan), 0).reset_index(drop=True)

output_df = PolynomialFeatures_labeled(X[X.columns],2)
output_df_t = PolynomialFeatures_labeled(X_total[X.columns],2)

pca = PCA(n_components=1)
X['pca'] = pca.fit_transform(output_df)
X_total['pca'] = pca.transform(output_df_t)

print(f"X shape PolynomialFeatures_labeled :{X.shape} , y shape :{y.shape}")
print(f"X_total shape :{X_total.shape}")
print(f'Columns: {X.columns}')

X shape PolynomialFeatures_labeled :(188533, 18) , y shape :(188533,)
X_total shape :(125690, 18)
Columns: Index(['brand', 'model', 'model_year', 'milage', 'fuel_type', 'engine',
       'transmission', 'ext_col', 'int_col', 'accident', 'clean_title',
       'Vehicle_Age', 'Mileage_per_Year', 'milage_with_age',
       'Mileage_per_Year_with_age', 'horsepower', 'engine_dis_L', 'pca'],
      dtype='object')


In [17]:
for i in numetric_list:
    X[i+'+log'] = (X[i]+1).transform(np.log)
    X_total[i+'+log'] =(X_total[i]+1).transform(np.log)

    X[i+'+log1'] = (X[i]+1).transform(np.log1p)
    X_total[i+'+log1'] =(X_total[i]+1).transform(np.log1p)

    X[i+'+sqrt'] = (X[i]+1).transform(np.sqrt)
    X_total[i+'+sqrt'] =(X_total[i]+1).transform(np.sqrt)
            
for col in numetric_list:
    X[f'{col}_binned'] = pd.cut(X[col], bins=10, labels=False)
    X_total[f'{col}_binned'] = pd.cut(X_total[col], bins=10, labels=False)   

print(f"X shape :{X.shape} , y shape :{y.shape}")
print(f"X_total shape :{X_total.shape}")
print(f'Columns: {X.columns}')

X shape :(188533, 50) , y shape :(188533,)
X_total shape :(125690, 50)
Columns: Index(['brand', 'model', 'model_year', 'milage', 'fuel_type', 'engine',
       'transmission', 'ext_col', 'int_col', 'accident', 'clean_title',
       'Vehicle_Age', 'Mileage_per_Year', 'milage_with_age',
       'Mileage_per_Year_with_age', 'horsepower', 'engine_dis_L', 'pca',
       'model_year+log', 'model_year+log1', 'model_year+sqrt', 'milage+log',
       'milage+log1', 'milage+sqrt', 'Vehicle_Age+log', 'Vehicle_Age+log1',
       'Vehicle_Age+sqrt', 'Mileage_per_Year+log', 'Mileage_per_Year+log1',
       'Mileage_per_Year+sqrt', 'milage_with_age+log', 'milage_with_age+log1',
       'milage_with_age+sqrt', 'Mileage_per_Year_with_age+log',
       'Mileage_per_Year_with_age+log1', 'Mileage_per_Year_with_age+sqrt',
       'horsepower+log', 'horsepower+log1', 'horsepower+sqrt',
       'engine_dis_L+log', 'engine_dis_L+log1', 'engine_dis_L+sqrt',
       'model_year_binned', 'milage_binned', 'Vehicle_Age_binne

# Select Feature

In [18]:
X = variance_threshold(X,0.02)
list_name = (X.columns)
X_total = X_total[list_name]

print('Shape threshold X =', X.shape,',',"Shape X_total =", X_total.shape)
print(f'Columns: {X.columns}')

Shape threshold X = (188533, 47) , Shape X_total = (125690, 47)
Columns: Index(['brand', 'model', 'model_year', 'milage', 'fuel_type', 'engine',
       'transmission', 'ext_col', 'int_col', 'accident', 'clean_title',
       'Vehicle_Age', 'Mileage_per_Year', 'milage_with_age',
       'Mileage_per_Year_with_age', 'horsepower', 'engine_dis_L', 'pca',
       'milage+log', 'milage+log1', 'milage+sqrt', 'Vehicle_Age+log',
       'Vehicle_Age+log1', 'Vehicle_Age+sqrt', 'Mileage_per_Year+log',
       'Mileage_per_Year+log1', 'Mileage_per_Year+sqrt', 'milage_with_age+log',
       'milage_with_age+log1', 'milage_with_age+sqrt',
       'Mileage_per_Year_with_age+log', 'Mileage_per_Year_with_age+log1',
       'Mileage_per_Year_with_age+sqrt', 'horsepower+log', 'horsepower+log1',
       'horsepower+sqrt', 'engine_dis_L+log', 'engine_dis_L+log1',
       'engine_dis_L+sqrt', 'model_year_binned', 'milage_binned',
       'Vehicle_Age_binned', 'Mileage_per_Year_binned',
       'milage_with_age_binned',

In [19]:
model = xgb.XGBRegressor(random_state=random_state)
model.fit(X, y)
importances = model.feature_importances_
indices = np.argsort(importances)[::-1]
indices
X_sorted = X.iloc[:, indices]
X_total_sorted = X_total.iloc[:, indices]
print('Shape threshold X =', X_sorted.shape,',',"Shape X_total =", X_total_sorted.shape)
print(f'Columns: {X_sorted.columns}')

Shape threshold X = (188533, 47) , Shape X_total = (125690, 47)
Columns: Index(['milage', 'pca', 'milage_with_age', 'engine', 'ext_col', 'model_year',
       'int_col', 'model', 'fuel_type', 'brand', 'transmission',
       'engine_dis_L', 'clean_title', 'accident', 'Mileage_per_Year',
       'horsepower', 'Mileage_per_Year_with_age', 'horsepower_binned',
       'Mileage_per_Year_binned', 'milage_binned', 'Vehicle_Age',
       'Vehicle_Age+log', 'milage+log', 'milage+log1', 'milage+sqrt',
       'engine_dis_L_binned', 'Vehicle_Age+log1', 'horsepower+log1',
       'Mileage_per_Year_with_age_binned', 'milage_with_age_binned',
       'Vehicle_Age_binned', 'model_year_binned', 'engine_dis_L+sqrt',
       'engine_dis_L+log1', 'engine_dis_L+log', 'horsepower+sqrt',
       'horsepower+log', 'Mileage_per_Year+log',
       'Mileage_per_Year_with_age+sqrt', 'Mileage_per_Year_with_age+log1',
       'Mileage_per_Year_with_age+log', 'milage_with_age+sqrt',
       'milage_with_age+log1', 'milage_with

In [20]:
df = pd.DataFrame(X_sorted, columns=X_sorted.columns)
df['target'] = y
corr = df.corr()
target_corr = corr['target'].drop('target')
important_features = target_corr[abs(target_corr) > 0.09].index

X_cor = X_sorted.loc[:, important_features] 
X_total_cor = X_total_sorted.loc[:, important_features] 

print('Shape threshold X =', X_sorted.shape,',',"Shape X_total =", X_total_sorted.shape)
print(f'Columns: {X_sorted.columns}')

Shape threshold X = (188533, 47) , Shape X_total = (125690, 47)
Columns: Index(['milage', 'pca', 'milage_with_age', 'engine', 'ext_col', 'model_year',
       'int_col', 'model', 'fuel_type', 'brand', 'transmission',
       'engine_dis_L', 'clean_title', 'accident', 'Mileage_per_Year',
       'horsepower', 'Mileage_per_Year_with_age', 'horsepower_binned',
       'Mileage_per_Year_binned', 'milage_binned', 'Vehicle_Age',
       'Vehicle_Age+log', 'milage+log', 'milage+log1', 'milage+sqrt',
       'engine_dis_L_binned', 'Vehicle_Age+log1', 'horsepower+log1',
       'Mileage_per_Year_with_age_binned', 'milage_with_age_binned',
       'Vehicle_Age_binned', 'model_year_binned', 'engine_dis_L+sqrt',
       'engine_dis_L+log1', 'engine_dis_L+log', 'horsepower+sqrt',
       'horsepower+log', 'Mileage_per_Year+log',
       'Mileage_per_Year_with_age+sqrt', 'Mileage_per_Year_with_age+log1',
       'Mileage_per_Year_with_age+log', 'milage_with_age+sqrt',
       'milage_with_age+log1', 'milage_with

In [21]:
F_values, p_values = f_regression(X_cor, y)
k = 35

top_k_indices = np.argsort(F_values)[::-1][:k]

X = X_cor.iloc[:, top_k_indices]
X_total = X_total_cor.iloc[:, top_k_indices]

print('Shape threshold X =', X.shape,',',"Shape X_total =", X_total.shape)
print(f'Columns: {X.columns}')

Shape threshold X = (188533, 29) , Shape X_total = (125690, 29)
Columns: Index(['milage+sqrt', 'milage+log1', 'milage+log', 'milage',
       'milage_with_age+log1', 'milage_with_age+log', 'milage_with_age+sqrt',
       'milage_binned', 'Vehicle_Age+log', 'Vehicle_Age+log1',
       'milage_with_age', 'milage_with_age_binned', 'Vehicle_Age+sqrt', 'pca',
       'Vehicle_Age', 'model_year', 'model_year_binned', 'Vehicle_Age_binned',
       'engine', 'Mileage_per_Year+log1', 'Mileage_per_Year+log',
       'Mileage_per_Year+sqrt', 'Mileage_per_Year_with_age',
       'Mileage_per_Year_with_age_binned', 'engine_dis_L_binned',
       'Mileage_per_Year_with_age+sqrt', 'accident', 'engine_dis_L',
       'Mileage_per_Year'],
      dtype='object')


In [22]:
model = LinearRegression()
sfs = SequentialFeatureSelector(model, n_features_to_select='auto', direction='forward', scoring = 'neg_root_mean_squared_error')
sfs.fit(X, y)

selected_features = sfs.support_
X_sfs = X.loc[:, selected_features] 
X_total_sfs = X_total.loc[:, selected_features] 

print('Shape threshold X =', X_sfs.shape,',',"Shape X_total =", X_total_sfs.shape)
print(f'Columns: {X_sfs.columns}')

Shape threshold X = (188533, 14) , Shape X_total = (125690, 14)
Columns: Index(['milage+sqrt', 'milage+log', 'milage', 'pca', 'Vehicle_Age',
       'model_year_binned', 'Vehicle_Age_binned', 'engine',
       'Mileage_per_Year+sqrt', 'Mileage_per_Year_with_age',
       'Mileage_per_Year_with_age_binned', 'engine_dis_L_binned', 'accident',
       'engine_dis_L'],
      dtype='object')


In [23]:
scaler = StandardScaler()
X = scaler.fit_transform(X_sfs)
X_total = scaler.transform(X_total_sfs)

In [24]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.33, random_state=random_state)

# Optuna serch

In [25]:
def objective_catboost(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 2500),
        'depth': trial.suggest_int('depth', 2, 15),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-4, 1e-1),
        'l2_leaf_reg': trial.suggest_loguniform('l2_leaf_reg', 1e-3, 10.0),
        'random_strength': trial.suggest_loguniform('random_strength', 1e-9, 10.0),
        'max_bin': trial.suggest_int('max_bin', 32, 255),
        'leaf_estimation_iterations': trial.suggest_int('leaf_estimation_iterations', 1, 10),
        'verbose': 0,
#         'task_type': 'GPU',  
#         'devices': '0' 
    }
    
    model = CatBoostRegressor(**params)
    model.fit(X_train, y_train, eval_set=(X_test, y_test), early_stopping_rounds=50, use_best_model=True, verbose=0)
    y_pred = model.predict(X_test)
    
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    return rmse


study_catboost = optuna.create_study(direction='minimize')
study_catboost.optimize(objective_catboost, n_trials=100)

cat_param = study_catboost.best_params
print("Best hyperparameters for CatBoost:", study_catboost.best_params)
print("Best RMSE score for CatBoost:", study_catboost.best_value)

[I 2024-09-12 07:26:38,985] A new study created in memory with name: no-name-761a89be-ee41-47c0-a14b-0f0f8be6534f
[I 2024-09-12 07:27:19,836] Trial 0 finished with value: 70485.80199172208 and parameters: {'iterations': 649, 'depth': 11, 'learning_rate': 0.0005589314606106945, 'l2_leaf_reg': 0.02786824016565398, 'random_strength': 2.394594499746046, 'max_bin': 120, 'leaf_estimation_iterations': 3}. Best is trial 0 with value: 70485.80199172208.
[I 2024-09-12 07:28:22,719] Trial 1 finished with value: 68050.92378888444 and parameters: {'iterations': 2409, 'depth': 9, 'learning_rate': 0.0005333336385287189, 'l2_leaf_reg': 0.10898206364296678, 'random_strength': 1.1340566429131533e-05, 'max_bin': 44, 'leaf_estimation_iterations': 3}. Best is trial 1 with value: 68050.92378888444.
[I 2024-09-12 07:30:03,079] Trial 2 finished with value: 69276.24315383098 and parameters: {'iterations': 1512, 'depth': 11, 'learning_rate': 0.000413581741051722, 'l2_leaf_reg': 0.00827339793149472, 'random_stre

Best hyperparameters for CatBoost: {'iterations': 1401, 'depth': 3, 'learning_rate': 0.05781488659646188, 'l2_leaf_reg': 0.01766570556414018, 'random_strength': 0.00014698768266656562, 'max_bin': 228, 'leaf_estimation_iterations': 10}
Best RMSE score for CatBoost: 67174.95308816427


In [26]:
def objective_xgboost(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 2500),  
        'max_depth': trial.suggest_int('max_depth', 2, 15),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-4, 1e-1),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_loguniform('gamma', 1e-3, 10.0),
        'lambda': trial.suggest_loguniform('lambda', 1e-3, 10.0),
        'alpha': trial.suggest_loguniform('alpha', 1e-3, 10.0),
        'verbosity': 0,
#         'tree_method': 'gpu_hist'
    }

    model = xgb.XGBRegressor(**params)
    model.fit(X_train, y_train,
              eval_set=[(X_test, y_test)],
              early_stopping_rounds=100,  
              verbose=0)
    
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    
    return rmse

study_xgboost = optuna.create_study(direction='minimize')
study_xgboost.optimize(objective_xgboost, n_trials=50)

xgb_param = study_xgboost.best_params
print("Best hyperparameters for XGBoost:", study_xgboost.best_params)
print("Best RMSE score for XGBoost:", study_xgboost.best_value)

[I 2024-09-12 08:04:00,984] A new study created in memory with name: no-name-e65a8510-11ad-4b75-b2a9-02cd67278e92
[I 2024-09-12 08:04:08,681] Trial 0 finished with value: 70694.44981413448 and parameters: {'n_estimators': 2282, 'max_depth': 15, 'learning_rate': 0.09323581277575088, 'subsample': 0.5163533366800004, 'colsample_bytree': 0.750005343738848, 'gamma': 4.943511960172559, 'lambda': 0.0016458948225180072, 'alpha': 1.2801159456174271}. Best is trial 0 with value: 70694.44981413448.
[I 2024-09-12 08:04:48,194] Trial 1 finished with value: 69348.80048382639 and parameters: {'n_estimators': 2381, 'max_depth': 10, 'learning_rate': 0.0009185040296272463, 'subsample': 0.969736515756211, 'colsample_bytree': 0.7907475207492021, 'gamma': 3.066265767882925, 'lambda': 0.018251036357374992, 'alpha': 1.4919453230813982}. Best is trial 1 with value: 69348.80048382639.
[I 2024-09-12 08:05:07,732] Trial 2 finished with value: 71689.05811430978 and parameters: {'n_estimators': 1180, 'max_depth': 

Best hyperparameters for XGBoost: {'n_estimators': 1682, 'max_depth': 3, 'learning_rate': 0.024440128654794946, 'subsample': 0.8531037952741702, 'colsample_bytree': 0.7634771255740845, 'gamma': 8.544369987268205, 'lambda': 9.938310238260105, 'alpha': 0.8451855845866841}
Best RMSE score for XGBoost: 67086.83670654868


In [27]:
def objective_lgbm(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 2500),  
        'max_depth': trial.suggest_int('max_depth', 2, 15),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-4, 1e-1),
        'num_leaves': trial.suggest_int('num_leaves', 20, 256),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'lambda_l1': trial.suggest_loguniform('lambda_l1', 1e-3, 10.0),
        'lambda_l2': trial.suggest_loguniform('lambda_l2', 1e-3, 10.0),
#         'device': 'gpu'
    }

    model = LGBMRegressor(**params, early_stopping_rounds=100, verbose = -1)
    model.fit(X_train, y_train,
              eval_set=[(X_test, y_test)])
    
    y_pred = model.predict(X_test)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    
    return rmse


study_lgbm = optuna.create_study(direction='minimize')
study_lgbm.optimize(objective_lgbm, n_trials=50)

lgbm_param = study_lgbm.best_params
print("Best hyperparameters for LGBM:", study_lgbm.best_params)
print("Best RMSE score for LGBM:", study_lgbm.best_value)

[I 2024-09-12 08:16:34,690] A new study created in memory with name: no-name-3ebfe7d2-7bdf-4879-a919-f5ccdb8cffe7
[I 2024-09-12 08:18:19,996] Trial 0 finished with value: 68435.29219843066 and parameters: {'n_estimators': 1937, 'max_depth': 14, 'learning_rate': 0.00042086972651622027, 'num_leaves': 213, 'subsample': 0.786498831679284, 'colsample_bytree': 0.8425800905519647, 'lambda_l1': 0.014004009287824628, 'lambda_l2': 0.9575073104336459}. Best is trial 0 with value: 68435.29219843066.
[I 2024-09-12 08:18:52,593] Trial 1 finished with value: 67552.06919179796 and parameters: {'n_estimators': 1021, 'max_depth': 8, 'learning_rate': 0.0016322992130398644, 'num_leaves': 32, 'subsample': 0.6374548353797282, 'colsample_bytree': 0.7659093115052965, 'lambda_l1': 0.19564416941108528, 'lambda_l2': 0.1524203376726928}. Best is trial 1 with value: 67552.06919179796.
[I 2024-09-12 08:19:03,980] Trial 2 finished with value: 67302.90155011702 and parameters: {'n_estimators': 877, 'max_depth': 2, 'l

Best hyperparameters for LGBM: {'n_estimators': 2326, 'max_depth': 5, 'learning_rate': 0.02372559651900322, 'num_leaves': 200, 'subsample': 0.857156350829974, 'colsample_bytree': 0.6757160606943383, 'lambda_l1': 4.261452942170477, 'lambda_l2': 0.002108595148826913}
Best RMSE score for LGBM: 67014.45118067916


# Set parametrs

In [28]:
lgbm_param1 = {'n_estimators': 100, 'max_depth': 4, 'learning_rate': 0.09099608165561339, 
              'num_leaves': 78, 'subsample': 0.954794300290001, 'colsample_bytree': 0.9086865204712623, 
              'lambda_l1': 0.04846898189883044, 'lambda_l2': 0.006319854565365427}

xgb_param1 = {'n_estimators': 1328, 'max_depth': 3, 'learning_rate': 0.025485055798334582,
             'subsample': 0.7566303135093686, 'colsample_bytree': 0.5309208920325769, 
             'gamma': 5.930100022955942, 'lambda': 9.209310540247191, 'alpha': 0.07378057402680178}

cat_param1 = {'iterations': 1490, 'depth': 4, 'learning_rate': 0.03270834072090292,
'l2_leaf_reg': 0.0010465472488675096, 'random_strength': 0.00018854204007994515, 
        'max_bin': 248, 'leaf_estimation_iterations': 9}

# Keras strategy

In [29]:
try:
    tpu = tf.distribute.cluster_resolver.TPUClusterResolver() # TPU detection
except ValueError:
    tpu = None
    gpus = tf.config.experimental.list_logical_devices("GPU")
    
if tpu:
    tf.tpu.experimental.initialize_tpu_system(tpu)
    strategy = tf.distribute.experimental.TPUStrategy(tpu,) 
    print('Running on TPU ', tpu.cluster_spec().as_dict()['worker'])
elif len(gpus) > 1:
    strategy = tf.distribute.MirroredStrategy([gpu.name for gpu in gpus])
    print('Running on multiple GPUs ', [gpu.name for gpu in gpus])
elif len(gpus) == 1:
    strategy = tf.distribute.get_strategy() 
    print('Running on single GPU ', gpus[0].name)
else:
    strategy = tf.distribute.get_strategy() 
    print('Running on CPU')
print("Number of accelerators: ", strategy.num_replicas_in_sync)

Running on CPU
Number of accelerators:  1


In [30]:
# Define the metric function if not defined
def metric(y_true, y_pred):
    return mean_absolute_error(y_true, y_pred)

In [31]:
# Define your create_model function for Keras
def create_model():
    model = Sequential()
    model.add(Dense(64, input_dim=X_train.shape[1], activation='relu'))
    model.add(Dense(32, activation='relu'))
    model.add(Dense(1, activation='linear'))
    model.compile(optimizer='adam', loss='mean_absolute_error')
    return model

# Fit model + Keras magik

In [32]:
# Initialize arrays for storing predictions
oof_preds = pd.DataFrame({
    'cat': np.zeros(len(X)),
    'xgb': np.zeros(len(X)),
    'lgb': np.zeros(len(X)),
    'hgb': np.zeros(len(X)),
    'network': np.zeros(len(X)),
    'cat1': np.zeros(len(X)),
    'xgb1': np.zeros(len(X)),
    'lgb1': np.zeros(len(X))
 })
test_preds = pd.DataFrame({
    'cat': np.zeros(len(X_total)),
    'xgb': np.zeros(len(X_total)),
    'lgb': np.zeros(len(X_total)),
    'hgb': np.zeros(len(X_total)),
    'network': np.zeros(len(X_total)),
    'cat1': np.zeros(len(X_total)),
    'xgb1': np.zeros(len(X_total)),
    'lgb1': np.zeros(len(X_total)),
})
ensemble_score = []
weights = []
test_predss = np.zeros(len(X_total))

# Split the data and train models
FOLDs = KFold(n_splits=n_splits, shuffle=True, random_state=random_state)

for fold_, (trn_idx, val_idx) in enumerate(FOLDs.split(X, y)):
    x_train, x_val = X[trn_idx], X[val_idx]
    y_train, y_val = y[trn_idx], y[val_idx]
    
    # Keras Model
    model = create_model()
    early_stopping = keras.callbacks.EarlyStopping(monitor="val_loss", patience=10, min_delta=0.001, restore_best_weights=True)
    reduce_lr = keras.callbacks.ReduceLROnPlateau(factor=0.1, patience=15, mode='min', verbose=1)
    model.fit(x_train, y_train, batch_size=250, epochs=50, validation_data=(x_val, y_val), callbacks=[reduce_lr, early_stopping])
    oof_preds['network'][val_idx] = model.predict(x_val).flatten()
    test_preds['network'] += model.predict(X_total).flatten() / FOLDs.n_splits
    network_score = mean_absolute_error(y_val, oof_preds['network'][val_idx])
    print(f'Fold {fold_} -- Keras oof MAE is --- {network_score:.4f}')

    # CatBoost
    cat_model = CatBoostRegressor(**cat_param, verbose=0)
    cat_model.fit(x_train, y_train)
    oof_preds['cat'][val_idx] = cat_model.predict(x_val)
    test_preds['cat'] += cat_model.predict(X_total) / FOLDs.n_splits
    cat_score = mean_absolute_error(oof_preds['cat'][val_idx], y_val)
    print(f'Fold {fold_} -- CatBoostRegressor oof MAE is --- {cat_score:.4f}')
    
    # XGBoost
    xgb_model = xgb.XGBRegressor(**xgb_param)
    xgb_model.fit(x_train, y_train)
    oof_preds['xgb'][val_idx] = xgb_model.predict(x_val)
    test_preds['xgb'] += xgb_model.predict(X_total) / FOLDs.n_splits
    xgb_score = mean_absolute_error(oof_preds['xgb'][val_idx], y_val)
    print(f'Fold {fold_} -- XGBRegressor oof MAE is --- {xgb_score:.4f}')
    
    # LightGBM
    lgb_model = LGBMRegressor(**lgbm_param, early_stopping_rounds=50, verbose = -1)
    lgb_model.fit(x_train, y_train,
              eval_set=[(x_val, y_val)])
    oof_preds['lgb'][val_idx] = lgb_model.predict(x_val)
    test_preds['lgb'] += lgb_model.predict(X_total) / FOLDs.n_splits
    lgb_score = mean_absolute_error(oof_preds['lgb'][val_idx], y_val)
    print(f'Fold {fold_} -- LGBMRegressor oof MAE is --- {lgb_score:.4f}')
    
    
    # HistGradientBoosting
    hgb_model = HistGradientBoostingRegressor()
    hgb_model.fit(x_train, y_train)
    oof_preds['hgb'][val_idx] = hgb_model.predict(x_val)
    test_preds['hgb'] += hgb_model.predict(X_total) / FOLDs.n_splits
    hgb_score = mean_absolute_error(oof_preds['hgb'][val_idx], y_val)
    print(f'Fold {fold_} -- HistGradientBoostingRegressor oof MAE is --- {hgb_score:.4f}')

    ensemble_score.append({'fold': fold_, 
                           'network': network_score, 
                           'cat': cat_score, 
                           'xgb': xgb_score, 
                           'lgb': lgb_score,
                           'hgb': hgb_score})
    
    # CatBoost
    cat_model1 = CatBoostRegressor(**cat_param1, verbose=0)
    cat_model1.fit(x_train, y_train)
    oof_preds['cat1'][val_idx] = cat_model1.predict(x_val)
    test_preds['cat1'] += cat_model1.predict(X_total) / FOLDs.n_splits
    cat_score1 = mean_absolute_error(oof_preds['cat1'][val_idx], y_val)
    print(f'Fold {fold_} -- CatBoostRegressor oof MAE is --- {cat_score1:.4f}')
    
    # XGBoost
    xgb_model1 = xgb.XGBRegressor(**xgb_param1)
    xgb_model1.fit(x_train, y_train)
    oof_preds['xgb1'][val_idx] = xgb_model1.predict(x_val)
    test_preds['xgb1'] += xgb_model1.predict(X_total) / FOLDs.n_splits
    xgb_score1 = mean_absolute_error(oof_preds['xgb1'][val_idx], y_val)
    print(f'Fold {fold_} -- XGBRegressor oof MAE is --- {xgb_score1:.4f}')
    
    # LightGBM
    lgb_model1 = LGBMRegressor(**lgbm_param1, early_stopping_rounds=50, verbose = -1)
    lgb_model1.fit(x_train, y_train,
              eval_set=[(x_val, y_val)])
    oof_preds['lgb1'][val_idx] = lgb_model1.predict(x_val)
    test_preds['lgb1'] += lgb_model1.predict(X_total) / FOLDs.n_splits
    lgb_score1 = mean_absolute_error(oof_preds['lgb1'][val_idx], y_val)
    print(f'Fold {fold_} -- LGBMRegressor oof MAE is --- {lgb_score1:.4f}')


Epoch 1/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 43611.9336 - val_loss: 37299.8516 - learning_rate: 0.0010
Epoch 2/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step - loss: 32884.4688 - val_loss: 21467.1953 - learning_rate: 0.0010
Epoch 3/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 20760.7285 - val_loss: 19996.5273 - learning_rate: 0.0010
Epoch 4/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 20173.2266 - val_loss: 19134.9316 - learning_rate: 0.0010
Epoch 5/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step - loss: 19531.6895 - val_loss: 18722.6094 - learning_rate: 0.0010
Epoch 6/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 18998.8750 - val_loss: 18502.7012 - learning_rate: 0.0010
Epoch 7/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 18471.6504 - val_loss: 18383.2148 - learning_rate: 0.0010
Epoch 8/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - loss: 18323.2402 - val_loss: 18320.2793 - learning_rate: 0.0010
Epoch 9/50
604/604 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - lo

# Blend

In [33]:
FOLDs = KFold(n_splits=n_splits, shuffle=True, random_state=random_state)

oof_blend = np.zeros(len(oof_preds))
predictions_blend = np.zeros(len(test_preds))

for fold_, (trn_idx, val_idx) in enumerate(FOLDs.split(oof_preds, y)):
    x_train, x_val = oof_preds.iloc[trn_idx], oof_preds.iloc[val_idx]
    y_train, y_val = y.iloc[trn_idx], y.iloc[val_idx]
    
    gb_model = GradientBoostingRegressor(n_estimators=1000, learning_rate=0.1, max_depth=3, random_state=random_state)
    gb_model.fit(x_train, y_train)
    
    oof_blend[val_idx] = gb_model.predict(x_val)
    predictions_blend += gb_model.predict(test_preds) / FOLDs.n_splits
    
    gb_score = mean_absolute_error(y_val, oof_blend[val_idx])
    print(f'Fold {fold_} -- GradientBoostingRegressor oof MAE is --- {gb_score:.4f}')

print(f'Final MAE of Gradient Boosting Blending Model: {mean_absolute_error(y, oof_blend):.4f}')

Fold 0 -- GradientBoostingRegressor oof MAE is --- 20368.1830
Fold 1 -- GradientBoostingRegressor oof MAE is --- 19983.2503
Fold 2 -- GradientBoostingRegressor oof MAE is --- 20320.4153
Fold 3 -- GradientBoostingRegressor oof MAE is --- 20552.7912
Fold 4 -- GradientBoostingRegressor oof MAE is --- 20131.8626
Final MAE of Gradient Boosting Blending Model: 20271.2997


# Submit

In [34]:
sample = pd.read_csv('/kaggle/input/playground-series-s4e9/sample_submission.csv')

In [35]:
sample['price'] = predictions_blend
sample.to_csv('submission.csv', index=False)